<a href="https://colab.research.google.com/github/SAWGraph/public/blob/main/UC1_CQ3b%2C5_query.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Intro

The purpose of this notebook is to query the SAWGraph knowledge graph for wells that are connected via aquifers to private water supply wells with high PFOA concentration results.

This is a demonstration of comepetency questions 3b and 5 from Use Case 1: Testing.

- What wells are hydrologically connected to PFOA contaminated private water supply wells where results have been above 200 ng/L?
  - Original Q3b: What wells are near locations with a reported PFOA contamination above 4ppt?
  - Original Q5: What wells are hydrologically connected to other wells with a reported contamination of above 10ppt?

# Setup

Here we set up SPARQLWrapper to work with our endpoint and create our query.

## Install & Import Statements

Install: The SPARQLWrapper libary provides tools for querying SPARQL endpoints. The sparql_dataframe library can be used with SPARQLWrapper to convert JSON results from a SPARQL query directly to a Pandas dataframe. The mapclassify library is required by GeoPandas for its .explore functionality.

Import: See the inline comments for a brief rationale of each library.

In [ ]:
%%capture
!pip install mapclassify --upgrade --quiet
!pip install SPARQLWrapper --upgrade --quiet
!pip install sparql_dataframe --upgrade --quiet

In [ ]:
from branca.element import Figure                                  # For controlling the size of the final map
import folium                                                      # For map layer control
import geopandas as gpd                                            # For geospatial dataframes
import pandas as pd                                                # For dataframes
from shapely import wkt                                            # For working with WKT coordinates in a GeoDataFrame
from SPARQLWrapper import SPARQLWrapper, JSON, GET, POST, DIGEST   # For querying SPARQL endpoints
import sparql_dataframe                                            # For converting SPARQL query results to Pandas dataframes

## Variable Initialization

A SPARQLWrapper is created to access the Hydrology repository for the SAWGraph project.

In [ ]:
%%capture
pd.options.display.width = 240
pd.options.mode.copy_on_write = True

endpointSAWGraph = 'https://gdb.acg.maine.edu:7200/repositories/SAWGraph'
sparqlSAWGraph = SPARQLWrapper(endpointSAWGraph)
sparqlSAWGraph.setHTTPAuth(DIGEST)
sparqlSAWGraph.setCredentials('sawgraph-endpoint', 'skailab')
sparqlSAWGraph.setMethod(GET)
sparqlSAWGraph.setReturnFormat(JSON)

endpointHydrology = 'https://gdb.acg.maine.edu:7200/repositories/Hydrology'
sparqlHydrology = SPARQLWrapper(endpointHydrology)
sparqlHydrology.setHTTPAuth(DIGEST)
sparqlHydrology.setCredentials('sawgraph-endpoint', 'skailab')
sparqlHydrology.setMethod(GET)
sparqlHydrology.setReturnFormat(JSON)

## Primary Query

This query directly accesses data in the SAWGraph repository of the SAWGraph Knowledge Graph. It uses federation to access additional data in the Hydrology repository.

The first block of the query
- finds EGAD sample points and restrict them to private water supply wells,
- finds PFOA observations and results for each EGAD sample point,
- finds PFOA levels for each result, limiting them to units of ng/L, and
- keeps only results over 200 ng/L PFOA.

The next line
- finds the S2 cell each private water supply well is within.

The federated portion
- finds aquifers that are coincident with the private water supply wells using the S2 cells, and
- finds all S2 cells that are within or overlap an aquifer.

The final block
- finds all wells that access the aquifers.

The query is executed and returned as a dataframe.

In [ ]:
%%time
query = """
PREFIX coso: <http://sawgraph.spatialai.org/v1/contaminoso#>
PREFIX geo: <http://www.opengis.net/ont/geosparql#>
PREFIX gwml: <http://www.opengis.net/gwml-main/2.2/>
PREFIX kwg-ont: <http://stko-kwg.geog.ucsb.edu/lod/ontology/>
PREFIX me_mgs: <http://sawgraph.spatialai.org/v1/me-mgs#>
PREFIX me_egad: <http://sawgraph.spatialai.org/v1/me-egad#>
PREFIX qudt: <http://qudt.org/schema/qudt/>
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
PREFIX sosa: <http://www.w3.org/ns/sosa/>
PREFIX unit: <http://qudt.org/vocab/unit>

SELECT * WHERE {
    ?samp_pt rdf:type me_egad:EGAD-SamplePoint ;
             me_egad:samplePointType me_egad:featureType.PWSW .
	?obs coso:observedAtSamplePoint ?samp_pt ;
    	 coso:ofSubstance me_egad:parameter.PFOA_A ;
    	 sosa:hasResult ?result .
    ?result qudt:quantityValue ?quant_val .
    ?quant_val qudt:numericValue ?num_val ;
    		   qudt:unit unit:NanoGM-PER-L .
    FILTER(?num_val > 200)

    ?samp_pt kwg-ont:sfWithin ?sp_s2 .

    SERVICE <repository:Hydrology> {
        SELECT * WHERE {
            ?sp_s2 kwg-ont:sfWithin | kwg-ont:sfOverlaps ?aq .
            ?aq rdf:type gwml:GW_Aquifer .
            ?aq_s2 kwg-ont:sfWithin | kwg-ont:sfOverlaps ?aq .
        }
    }

    ?well rdf:type me_mgs:MGS-Well .
    ?well kwg-ont:sfWithin ?aq_s2 .
}
"""
df = sparql_dataframe.get(endpointSAWGraph, query)

CPU times: user 325 ms, sys: 131 ms, total: 456 ms
Wall time: 19.7 s


## Geometry Queries

This is a function to create a query for geometries for a list of instances in a KG.

In [ ]:
def geo_query(data):
    instances = ''
    for d in data:
        instances += '<' + d + '>, '
    instances = instances[:-2]
    query = """
    PREFIX geo: <http://www.opengis.net/ont/geosparql#>

    SELECT * WHERE {
        ?x geo:hasGeometry/geo:asWKT ?wkt .
        FILTER (?x IN (""" + instances + """))
    }
    """
    return query

Create lists of aquifers, wells, and sample points.

In [ ]:
aquifers = []
wells = []
samp_pts = []
for row in df.itertuples():
    if row.aq not in aquifers:
        aquifers.append(row.aq)
    if row.well not in wells:
        wells.append(row.well)
    if row.samp_pt not in samp_pts:
        samp_pts.append(row.samp_pt)

For this query, the number of aquifers and sample points are small. However, the number of wells is large so it takes multiple queries to retrieve all of the geometries. While 100 may not be the maximum number of wells for which geometries can be retrieved at once, 100 works and does not take very long. The following function provides a single interface regardless of how many instances require geometries.

In [ ]:
def retrieve_geometries(instances, repo):
    if len(instances) < 101:
        query = geo_query(instances)
        return sparql_dataframe.get(repo, query)
    else:
        data_dict = {}
        for i in range(len(instances) // 100 + 1):
            data_dict[i] = instances[i * 100:(i + 1) * 100]
        df_dict = {}
        for k, v in data_dict.items():
            query = geo_query(v)
            df_temp = sparql_dataframe.get(repo, query)
            if k == 0:
                df_dict[k] = [df_temp.columns.values.tolist()] + df_temp.values.tolist()
            else:
                df_dict[k] = df_temp.values.tolist()
        data_list = []
        for k, v in df_dict.items():
            for item in v:
                data_list.append(item)
        df_geo = pd.DataFrame(data_list[1:], columns=data_list[0])
        df_geo.drop_duplicates(inplace=True)
        return df_geo

In [ ]:
%%time
df_aq_geo = retrieve_geometries(aquifers, endpointHydrology)
df_sp_geo = retrieve_geometries(samp_pts, endpointSAWGraph)
df_well_geo = retrieve_geometries(wells, endpointSAWGraph)

CPU times: user 601 ms, sys: 88.9 ms, total: 690 ms
Wall time: 5.74 s


We have to add the geometries to the primary query's dataframe of results. This is done using the following function, which is called three times in this case for three different geometry types (sample points, aquifers, and wells).

In [ ]:
def new_column(df_in, df_wkt, col_item, col_wkt):
    df_out = df_in.copy()
    df_out[col_wkt] = df_out[col_item]
    for row in df_wkt.itertuples():
        df_out.loc[df_out[col_wkt] == row.x, col_wkt] = row.wkt
    return df_out

In [ ]:
df = new_column(df, df_sp_geo, 'samp_pt', 'samp_pt_wkt')
df = new_column(df, df_aq_geo, 'aq', 'aq_wkt')
df = new_column(df, df_well_geo, 'well', 'well_wkt')

# Visualizing on a map

## Partioning the Query Results



The data is split into three separate themed dataframes, one for the sample points, one for the aquifers, and one for the wells.

The columns with WKT coordinates in each dataframe are converted to Shapely geometry objects prior to converting the dataframes to GeoDataFrames.

In [ ]:
df_sp = df[['samp_pt', 'samp_pt_wkt', 'num_val']].copy()
df_sp.drop_duplicates(inplace=True)
df_sp['samp_pt_wkt'] = df_sp['samp_pt_wkt'].apply(wkt.loads)

df_aq = df[['aq', 'aq_wkt']].copy()
df_aq.drop_duplicates(inplace=True)
df_aq['aq_wkt'] = df_aq['aq_wkt'].apply(wkt.loads)

df_wl = df[['well', 'well_wkt']].copy()
df_wl.drop_duplicates(inplace=True)
df_wl['well_wkt'] = df_wl['well_wkt'].apply(wkt.loads)

## Create GeoPandas dataframes for mapping

Convert the above dataframes to GeoDataFrames, setting the WKT columns as the geometry columns and setting the CRS to WGS 84.

In [ ]:
%%capture
gdf_sp = gpd.GeoDataFrame(df_sp, geometry='samp_pt_wkt')
gdf_sp.set_crs(epsg=4326, inplace=True, allow_override=True)

gdf_aq = gpd.GeoDataFrame(df_aq, geometry='aq_wkt')
gdf_aq.set_crs(epsg=4326, inplace=True, allow_override=True)

gdf_wl = gpd.GeoDataFrame(df_wl, geometry='well_wkt')
gdf_wl.set_crs(epsg=4326, inplace=True, allow_override=True)

## Create map with multiple layers

Each GeoDataFrame is a layer in the final map.

In [ ]:
%%capture
sp_color = 'red'
aq_color = 'blue'
wl_color = 'black'
boundweight = 5

map = gdf_aq.explore(color=aq_color,
                     style_kwds=dict(weight=boundweight),
                     tooltip=True,
                     name='Aquifers',
                     show=True)
gdf_wl.explore(m=map,
               color=wl_color,
               style_kwds=dict(weight=boundweight),
               tooltip=True,
               highlight=False,
               name='Wells',
               show=True)
gdf_sp.explore(m=map,
               color=sp_color,
               style_kwds=dict(weight=boundweight),
               tooltip=True,
               name='Contaminated Sample Points',
               show=True)


# folium.TileLayer("stamenterrain", show=False).add_to(map)
# folium.TileLayer("MapQuest Open Aerial", show=False).add_to(map)
folium.LayerControl(collapsed=False).add_to(map)

## Show map

The map is created inside a Figure box to control its size.

In [ ]:
map.save('SAWGraph_UC1_CQ3b,5_map.html')

fig = Figure(width=800, height=600)
fig.add_child(map)